In [2]:
# imports
import numpy as np
import pandas as pd
import hashlib
import pickle
from elasticsearch import Elasticsearch
from elasticsearch_dsl import Search, Q
from tqdm.auto import tqdm

In [3]:
# connect to local elastic search host
HOST = 'http://localhost:9200/'
es = Elasticsearch(hosts=[HOST], timeout=30) # , max_retries=10, retry_on_timeout=True
INDEX = 'info_clone'
INDEX2 = 'info_clone2'

In [35]:
es.ping()

True

In [4]:
dict_of_duplicate_docs = {}
# The following line defines the fields that will be used to determine if a document is a duplicate
keys_to_include_in_hash = ['markdown','comments', 'code']
# Process documents returned by the current search/scroll
def populate_dict_of_duplicate_docs(hits):
    for item in hits:
        _id = item["_id"]
        print(_id, end='\r')
        combined_key = ""
        for mykey in keys_to_include_in_hash:
            if mykey == 'markdown':
                mkdn = es.get(index='markdown', id=_id, ignore=[404])
                if '_source' in mkdn:
                    mkdnlist = mkdn['_source']['markdown']
                    combined_key += ''.join(str(i) for i in mkdnlist if i)
            elif mykey == 'comments':
                comments = es.get(index='comments2', id=_id, ignore=[404])
                if '_source' in comments:
                    cmtlist = comments['_source']['comments']
                    combined_key += ''.join(str(i) for i in cmtlist if i)
            else:
                code = es.get(index='code', id=_id, ignore=[404])
                if '_source' in code:              
                    combined_key += str(code['_source']['imports'])
                    combined_key += str(code['_source']['classes'])
                    combined_key += str(code['_source']['functions'])
        if combined_key != "":
            hashval = hashlib.md5(combined_key.encode('utf-8')).digest()
            # If the hashval is new, then we will create a new key
            # in the dict_of_duplicate_docs, which will be
            # assigned a value of an empty array.
            # We then immediately push the _id onto the array.
            # If hashval already exists, then
            # we will just push the new _id onto the existing array
            dict_of_duplicate_docs.setdefault(hashval, []).append(_id)
# Loop over all documents in the index, and populate the
# dict_of_duplicate_docs data structure.
def scroll_over_all_docs():
    data = es.search(index=INDEX2, _source_excludes=['code', 'language'], 
                     scroll='1m',  body={"query": {"match_all": {}}})
    # Get the scroll ID
    sid = data['_scroll_id']
    scroll_size = len(data['hits']['hits'])
    # Before scroll, process current batch of hits
    populate_dict_of_duplicate_docs(data['hits']['hits'])
    while scroll_size > 0:
        data = es.scroll(scroll_id=sid, scroll='2m')
        # Process current batch of hits
        populate_dict_of_duplicate_docs(data['hits']['hits'])
        # Update the scroll ID
        sid = data['_scroll_id']
        # Get the number of results that returned in the last scroll
        scroll_size = len(data['hits']['hits'])

In [41]:
ids_to_remove = []
def remove_duplicates():
    # Search through the hash of doc values to see if any
    # duplicate hashes have been found
    print(len(dict_of_duplicate_docs.items()))
    for hashval, array_of_ids in dict_of_duplicate_docs.items():
        if len(array_of_ids) > 1:
            print("********** Duplicate docs hash=%s **********" % hashval)
            # Get the documents that have mapped to the current hashval
            matching_docs = es.mget(index=INDEX2, body={"ids": array_of_ids})
            matching_mknd = es.mget(index="markdown", body={"ids": array_of_ids})
            matching_code = es.mget(index="code", body={"ids": array_of_ids})
            matching_cmts = es.mget(index="comments2", body={"ids": array_of_ids})
            dups = []
            ids = []
            for i in range(len(matching_docs['docs'])):
                ids.append(matching_docs['docs'][i]['_id'])
                markdown = matching_mknd['docs'][i]['_source']['markdown']
                comments = matching_cmts['docs'][i]['_source']['comments']
                imports = matching_code['docs'][i]['_source']['imports']
                classes = matching_code['docs'][i]['_source']['classes']
                functions = matching_code['docs'][i]['_source']['functions']
                dups.append((markdown,comments,imports,classes,functions))
            # if all documents are actually identical, remove all but one of them.
            if len(dups) > 0 and all(elem == dups[0] for elem in dups):
                ids.pop(0)
                ids_to_remove.extend(ids)
#         for doc in matching_docs['docs']:
#                 info = matching_docs['docs'][i]
            #print("doc=%s\n" % doc)
            # In order to remove the possibility of hash collisions,
            # write code here to check all fields in the docs to
            # see if they are truly identical - if so, then execute a
            # DELETE operation on all except one.
            # In this example, we just print the duplicate docs.
            # This code could be easily modified to delete duplicates
            # here instead of printing them

In [5]:
scroll_over_all_docs()

In [42]:
remove_duplicates()

691680
********** Duplicate docs hash=b' \x84\xc0Lpi\xf5\xbb\xc1K\xe4v]\x10w0' **********
********** Duplicate docs hash=b'\x18\x93=x\xf4\xb5lK\x85\xb4\x1aw\x1e1X]' **********
********** Duplicate docs hash=b' _)D\x8f\xeex\x7f\xf4\xfa$\x04\x06\x981\xe4' **********
********** Duplicate docs hash=b'oj\x8e\xa9\x11\xdb\x8b9\xa1*%mW\xad\xce\xab' **********
********** Duplicate docs hash=b'CT\x15\x15\xee\xe4\xb6\xe5\xd1x\x11\xd5\xdeZe\xe1' **********
********** Duplicate docs hash=b'\\\xc9\xe0G\x14\xb6g\xa2\xfdjtP\x16_&l' **********
********** Duplicate docs hash=b'\x9f?\x96\x8a\x86\xa2\xedb\xe4\x9f%\x85\x82T\xbai' **********
********** Duplicate docs hash=b'\xb4LXzx\xa7\x15\xfb3\x8aq\xe96b\xf8\x04' **********
********** Duplicate docs hash=b'x\xb6:\xd0~\x98\xaciS\x03\x8a\xfe\xbf\xc1#\xc5' **********
********** Duplicate docs hash=b'\xfeC\xd0\x85\xd6?\xd6\x07\xde[\xf0t\xf5*y\x8f' **********
********** Duplicate docs hash=b'~\xce\xe0Ay\xd8PS\xb0\xec\xa2\xf8\xbbq`w' **********
********** Dupli

********** Duplicate docs hash=b'DO!\xf8\xbd\xa0\x03X\x0es@\xee\xedbqc' **********
********** Duplicate docs hash=b'\x1ej`\xab\x1e\xfa\x17\xb5|\xe6iGVk\xdd\xbf' **********
********** Duplicate docs hash=b'\x0e\x8a\x9f\xc3g\x86\xca\x83\x00\xb5\x9a\xdd\xce\xe3\x84-' **********
********** Duplicate docs hash=b'\xcd\xfc,\x80\xf9\xf0@\x80|\xde\xf8(&\x04\xcd\x88' **********
********** Duplicate docs hash=b'xic\x95\xff\xcf\x06\xb3\xb5\xd5\xfe\x14|Z\xa6\x94' **********
********** Duplicate docs hash=b'\x9f+\xacY\x95\xc4\xcfw\x9d\x99\xd9\x9c\xddy\xac\x7f' **********
********** Duplicate docs hash=b'\xbex\xf1\x1f\xca\x12\t\xb3g5T\xbe\xf6\xe20\xc9' **********
********** Duplicate docs hash=b'.\xf6\xe7\x05oYH\x1d\\5\xa8\xfc\xdc\x15\x91!' **********
********** Duplicate docs hash=b'\xdf\xa2\xe1\xd3\xcag6eT\xc2l\x06{\x0e\xb6l' **********
********** Duplicate docs hash=b'\xff\x04\xa1qQ\x8d\x1f\x8e\x07=,Z\x0c\xf5JB' **********
********** Duplicate docs hash=b'\xd9\xb6@Un\x95\xbe\xf5\xecA\xfd\xb5j\xa7\

********** Duplicate docs hash=b'\x16_\x9a2Y:<\x8fY\x93\x18\x1f\x12\xa2\\$' **********
********** Duplicate docs hash=b'\\`\xc3r_\x1c\xfa\xef0\x07_\xb2K\xc5\xb1:' **********
********** Duplicate docs hash=b's\x85\x942\xea\x197\x12\xc4\x8d%\xfbJ\xb5\xfag' **********
********** Duplicate docs hash=b'\xb0\xf3\x9bd\x02\x18j\xc2!\x91A\xf8\x00\xe3Zl' **********
********** Duplicate docs hash=b'\xf7\x94\x08\xa0\x90\xc7\x0b_h\xd4gfg\xdb_\xc8' **********
********** Duplicate docs hash=b'K\xfa\x03?\xa5#\x1f\x8e\x9d\xdc\xf8\xc9\xb5@\xc1\x92' **********
********** Duplicate docs hash=b'\\V\xfb\xa1\x8f\x03v/\x1d\xebT\xdcw\x87\xeb\xad' **********
********** Duplicate docs hash=b'\x15\xe1\xed\x13\xd5\'\x81"Ww?=\x99\xbd\xb1\xaf' **********
********** Duplicate docs hash=b'\x8d\x1b\x7f\xe5\x9c3\xa3~\xf0\x1d\xbe\xa1>\x9f/\xbf' **********
********** Duplicate docs hash=b'\xb8\x8a\xd5\x95\xbd\x1e\x15\xfeb\r\xaeq\x86\x11|\xde' **********
********** Duplicate docs hash=b'1>\xea\xad%\xb1\x80\x1cJ\x13\x81\xbb

********** Duplicate docs hash=b'\xc7\xc8)\x1a\xfeu\xba\x16\xbe4L\x10{4\x03\xa3' **********
********** Duplicate docs hash=b'\xa6%R\xf6dP\x9d\xfd\xca_\xae\xce\x9e\x96{\x9c' **********
********** Duplicate docs hash=b':G\xdbk`c\x85\xe8\x80\xc5N\x14\x03i\xad$' **********
********** Duplicate docs hash=b'\xa7ig\xda\x9c\x10\x82\xdb\xe6|\xcf2\xa9\xd2\xba\xfa' **********
********** Duplicate docs hash=b"\xc2\xf0\xf8#\xe9'_\x8c\xaf*\xd4\x9d5\x96IB" **********
********** Duplicate docs hash=b'\xa4o\xcb\xb3\x01I\xd4\x10\xea\xab{\xb884\xfe>' **********
********** Duplicate docs hash=b'^\xc8NG\xadC"H\x82S2u\xdc@\xa9a' **********
********** Duplicate docs hash=b'\x97\xee\xee\xd2 \x1b\xcb\xa0e\xbe\x11"D\x1dk\x19' **********
********** Duplicate docs hash=b'\x01S/"Oq\\\x89vz\xf6V\x17E\xb5\xc3' **********
********** Duplicate docs hash=b'E\x04\x8e\xa6\x90x=?\x90.\xaf\xdd\xa8\xde\xd0D' **********
********** Duplicate docs hash=b'i7\x07\xbai`\x1a\xef\xb5\xe6\xd5\xb6\x14\xf2\x84_' **********
********** 

********** Duplicate docs hash=b'(\x81\xcfcFZs\xcc\xady\x94)\xd8\xc4\x8c\xe7' **********
********** Duplicate docs hash=b'\xcc\xd0\x94\xda\xab^\xbb84\x07g\xb0\xcb\x8d\x83\xd2' **********
********** Duplicate docs hash=b'\x1c\x99e\xc4|0\x9f\xbb\xce\x0f\x9d\x92)_\xf9y' **********
********** Duplicate docs hash=b'\x13hv\x0c\xa19\x0b\xad\xac\xd0\xa8V\x11\xb7\xcai' **********
********** Duplicate docs hash=b'G\x9f\xb4dK\x9b\xe3\x88\rL\x9b@N<\x9bh' **********
********** Duplicate docs hash=b'0\x04\xb4$\n\xfcb\xecH\xbe&5c\xe0\xcc\xb5' **********
********** Duplicate docs hash=b'\xcd=\xe8\x99\x07\xb9\xce\x86\x85\x92/s\xdbL\x03\xe7' **********
********** Duplicate docs hash=b'\x0b\xf7\xa2\xa4\xa9\xdb\xfa\xb1\x04\xb9h\xfd\xf9\xff\xb2\\' **********
********** Duplicate docs hash=b'\xbaH\x0eaAO):I\x00\x9c\xe75F\xf4\xd7' **********
********** Duplicate docs hash=b'\xa6\xa1"J>\xd5\xf6\xec\xc0\xc1%W\xe9\xe0\xf8J' **********
********** Duplicate docs hash=b' 4Y\xd7\xa0\xb8~\x1fz\xa6\xad\xb1\xaaM\x8f\x

...

********** Duplicate docs hash=b'\xe0\xaf\xd9\xc4\xdc\xa0\xe1\x1f?&\xcd\xe4\x0e\x7f\x13\x0c' **********
********** Duplicate docs hash=b"'\x8b\xd3\x12\xe6\xf9oa\x97\xb3\x08\xa7\xfel\xc9\xd9" **********
********** Duplicate docs hash=b'\x9cSf\xea\xae\xb3\x9e\xc4q\x9aZ\x18\xeeq\xdfp' **********
********** Duplicate docs hash=b'\x192I\x9c\xa0\xd3\xb4\x8a\xd7,\xb3=K@\x8c\xbe' **********
********** Duplicate docs hash=b'\r\x08\xe0\xf4\xeb\xef\xe1gv\xee\xe5\xac\x8f\x17<\xf7' **********
********** Duplicate docs hash=b'\xa6\x8d\xe3\xf1\xb0]\xfa\x9bBN\xcc\xbeh\xfd\x9fy' **********
********** Duplicate docs hash=b'M:t`\xe06DL\xc5\xdf4\n\xc9\x07=\x1c' **********
********** Duplicate docs hash=b'g\x00\xace}JR\x94\x94Z\xaf\xcf\x1c\tz\xf9' **********
********** Duplicate docs hash=b'y\xcdg;\xe8\x8f\xdbC\xe7)~@n\x84y\x8d' **********
********** Duplicate docs hash=b'K\xaf\x89\x03\x80\x9al\xde%\x8d\x0b\x06\x94D\xd0\xde' **********
********** Duplicate docs hash=b'\x81\x98\xc0cN.a\xbb\x9c\xb7\xe3 \xd1\

********** Duplicate docs hash=b'\xb4\xf91\xae\x8eJ\xfc\xa9\xa1[\xa0X\xe4\xec1\xdd' **********
********** Duplicate docs hash=b'r\xf9\xab\xce\n\x95Q\r\xb3\xbdxU\xec\x98\x86\x1f' **********
********** Duplicate docs hash=b'\x10V\xb5\x0b{\xa5\xae\xb0\xa9\x1e\x06\x19k\x96M\xbd' **********
********** Duplicate docs hash=b'\xd0\xbfKR1\x7f\xb1_\x17\xbf\x8a\xc6J.\xd8\xad' **********
********** Duplicate docs hash=b'\x92\xb5)x-[l%8:V3\xde\xa8\x9a\xe5' **********
********** Duplicate docs hash=b'\xbf\x9a\x89e2\xca\x90\x12J\xcf\xa0x\xe9]\xae\xa5' **********
********** Duplicate docs hash=b'[x\xbc%\xfa\x93B\xd4QH\x9a\xaf\xd6+\xdb|' **********
********** Duplicate docs hash=b'\xe9\xe0\xd9X\xb9Z\xc5`\xd2\x924\xec\x99\xf7E\xb1' **********
********** Duplicate docs hash=b'G\xae\xa9\xfb\xe2U5\xad1\x94f\xd2\x10o\xd6\xff' **********
********** Duplicate docs hash=b'H\x14n\x8dZ)\xbf/N0\x90\xe0N2c\x9d' **********
********** Duplicate docs hash=b'\x9c\x10\xab\xe4\x17c\xdc\xce^S\x1a\xd2\xa0\x15\xa3\x95' ***

********** Duplicate docs hash=b'\xbeG\xcc\xad\xb7\xf6T\xc7\xc5\xed\n\x8c\xad\xf2\xff\x06' **********
********** Duplicate docs hash=b'\x8e\x81\xbaa\xba\x1c\xc5\x05"W>3\x8fW+2' **********
********** Duplicate docs hash=b'\xfdW\x97\xdd\xf1\xe1:\x8d\xf6\xfc\xcfUGn\xd5\xa7' **********
********** Duplicate docs hash=b'\xcb\xf1\xd9\xd8\xbd\n\xf2\x8b\x91\xd5D\x16\xf9\xf7\x06%' **********
********** Duplicate docs hash=b'\xdcJ\xbf\nA|\xd27\xd9"\xa3s\xbd\x8e\xb7\xdc' **********
********** Duplicate docs hash=b'\xc8\x91\x00\x8f\x94\xdb\xdc\xb3\xb6\x92\x1f\xed\xbcw\x19\xf1' **********
********** Duplicate docs hash=b'-\xc0\xa0\x8a6\xab\x9e\xfd\xff@Ui\x08 \xfc.' **********
********** Duplicate docs hash=b'\x15\xa7gu\xbe\xe3q\x14\xcf\xc9\xacK\x01\\\x83\x98' **********
********** Duplicate docs hash=b'\xfe\xf8W\x9fp\xb9\xcf\x9e\xb5W\xdcV!\xca\xefJ' **********
********** Duplicate docs hash=b'\x04\x89\x87\xeb\xe9\xe1](\t\x14y\xfa\xce\x18\x14?' **********
********** Duplicate docs hash=b'X\x93\xcd_\x

********** Duplicate docs hash=b'zH\x12r9\xcf\xe7[\xd4!\xfc\x04\x99\xc5\xf8/' **********
********** Duplicate docs hash=b'\xd6\x10\xcc\xacK\xaf/\x0cNu6\xe6\xe2\xfd\x83\x07' **********
********** Duplicate docs hash=b'\xb9\xd6\xb2[\xfa\xe7\xcbW\xf7i\xbd\xa7)\xcc\x861' **********
********** Duplicate docs hash=b'$\xff\xcf\x1d\x1e\xca\x03B\xeef\x9fLD\x88\xf6\xc2' **********
********** Duplicate docs hash=b'\x16\xdd\x89\x14\xcd}\xf7\xf0 \x12`j^z;+' **********
********** Duplicate docs hash=b'DA\xddl-?\x11\xe7\xa6\x10\xc7\xbe\x00\xfe\x96\xb9' **********
********** Duplicate docs hash=b'#\xe1\xbcW\x13i\xfd\xea\x97\xbap\xbe\x05\xee_\xdc' **********
********** Duplicate docs hash=b'\t0\xbaU\x84\x9d\xce\x88\xd2+\xb1:\xe9H\xb9p' **********
********** Duplicate docs hash=b'(bi\xc8i\xeb>\xb4\xd7\xee9P\x1fVj\xdb' **********
********** Duplicate docs hash=b'\xcca\xea\xc8\x8a#VT\x8f\xbdG\x82V\xc5\x97\xf0' **********
********** Duplicate docs hash=b'\x16.C\xbc\xc4\xc9\x932\x0b\xb2;\x17\xc3nTj' *******

********** Duplicate docs hash=b'qa\\h\x1a\x92a9s\x97\x9d\x8a|t\xeeA' **********
********** Duplicate docs hash=b') ]\x9c\x0e\xff\xb8l\xeeA#\x8e\xd4\x0er\xa5' **********
********** Duplicate docs hash=b'\x9a\xb9C:pZO\x8c\xad\xfc\x12c1\xb6\x9fP' **********
********** Duplicate docs hash=b'\xbd\x06D\xb9\x8cM\xfa\x1buQ\x18o\x98jm\x14' **********
********** Duplicate docs hash=b'7\xc2\xd5\xae\xe4\xec\x9bA>\xb9\xeb\x1c\x9a0\x8e\xf3' **********
********** Duplicate docs hash=b'\x1e\xa3\x0b\xa5\xc6\x99\xee\xc0Z\xd3\x05t\xfb\x0f\n\xfa' **********
********** Duplicate docs hash=b'\xbd5\xa2\xbba%\xbdV\xbd\x86u\xe2ns\x8e\xe3' **********
********** Duplicate docs hash=b'bo\xf4l\xc22\xb3\xcfd\x9b\xe8{\x11\xe7&r' **********
********** Duplicate docs hash=b'\xd2\x9c\xfb\x08\xd8p\xb7\x94\xf9(i\x86\x9f\x9c>\x81' **********
********** Duplicate docs hash=b'\xe1\xdd\x0e\xb0\xde?\xf5\xea| \x00;Q3\x9a\x94' **********
********** Duplicate docs hash=b"'\xc93\xe1\xc3\x04\x90\x95\x071\xf9`L\x9er\xa4" *********

In [48]:
len(ids_to_remove)
# 1364 deleted for conn timeout total: 234472

234472

In [49]:
idsbody = {
    "query": {
        "ids" : {
        "values" : ids_to_remove
        }
    }    
}

es.delete_by_query(index=INDEX2, body=idsbody, ignore=[404])

{'batches': 0,
 'deleted': 0,
 'failures': [],
 'noops': 0,
 'requests_per_second': -1.0,
 'retries': {'bulk': 0, 'search': 0},
 'throttled_millis': 0,
 'throttled_until_millis': 0,
 'timed_out': False,
 'took': 706,
 'total': 0,
 'version_conflicts': 0}

In [50]:
with open('dupedict.pkl', 'wb') as f:
    pickle.dump(dict_of_duplicate_docs, f)

In [16]:
with open('dupedict.pkl', 'rb') as f:
     dict_of_duplicate_docs = pickle.load(f)

In [16]:
data = es.search(index="info_clone", scroll='1m',  body={"query": {"match_all": {}}})
s1 = data['_scroll_id']
s2 = len(data['hits']['hits'])
print(s1,s2)

DnF1ZXJ5VGhlbkZldGNoBQAAAAAAAAAVFlEzd2ozQW91UlJheWRZOUQ1ZDlXbkEAAAAAAAAAFhZRM3dqM0FvdVJSYXlkWTlENWQ5V25BAAAAAAAAABcWUTN3ajNBb3VSUmF5ZFk5RDVkOVduQQAAAAAAAAAYFlEzd2ozQW91UlJheWRZOUQ1ZDlXbkEAAAAAAAAAGRZRM3dqM0FvdVJSYXlkWTlENWQ5V25B 10


In [12]:
data = es.search(index="code",_source_excludes=['code', 'language'], scroll='1m',  body={"query": {"match_all": {}}})
s1 = data['_scroll_id']
s2 = len(data['hits']['hits'])
print(s1,s2)

DnF1ZXJ5VGhlbkZldGNoBQAAAAAAAAARFlEzd2ozQW91UlJheWRZOUQ1ZDlXbkEAAAAAAAAAExZRM3dqM0FvdVJSYXlkWTlENWQ5V25BAAAAAAAAABIWUTN3ajNBb3VSUmF5ZFk5RDVkOVduQQAAAAAAAAAQFlEzd2ozQW91UlJheWRZOUQ1ZDlXbkEAAAAAAAAAFBZRM3dqM0FvdVJSYXlkWTlENWQ5V25B 10


In [13]:
data['hits']['hits']

{'_scroll_id': 'DnF1ZXJ5VGhlbkZldGNoBQAAAAAAAAARFlEzd2ozQW91UlJheWRZOUQ1ZDlXbkEAAAAAAAAAExZRM3dqM0FvdVJSYXlkWTlENWQ5V25BAAAAAAAAABIWUTN3ajNBb3VSUmF5ZFk5RDVkOVduQQAAAAAAAAAQFlEzd2ozQW91UlJheWRZOUQ1ZDlXbkEAAAAAAAAAFBZRM3dqM0FvdVJSYXlkWTlENWQ5V25B',
 '_shards': {'failed': 0, 'skipped': 0, 'successful': 5, 'total': 5},
 'hits': {'hits': [{'_id': '68919',
    '_index': 'code',
    '_score': 1.0,
    '_source': {'classes': [],
     'functions': [],
     'imports': [['mpl_toolkits.basemap.Basemap', 'Basemap'],
      ['numpy', 'numpy']]},
    '_type': '_doc'},
   {'_id': '61052',
    '_index': 'code',
    '_score': 1.0,
    '_source': {'classes': [],
     'functions': [],
     'imports': [['urllib', 'urllib'],
      ['json', 'json'],
      ['urllib', 'urllib'],
      ['json', 'json'],
      ['urllib', 'urllib'],
      ['json', 'json'],
      ['urllib', 'urllib'],
      ['json', 'json']]},
    '_type': '_doc'},
   {'_id': '36912',
    '_index': 'code',
    '_score': 1.0,
    '_source': {'classe

In [37]:
n = [None]
''.join(i for i in n if i)

''

In [50]:
markdown = es.get(index='markdown', id=2161)
mdnlist = markdown['_source']['markdown']
print(mdnlist)

[['# Retrieving the data and storing it'], ["So we're going to `import` our HTML parser (`lxml.html`) and `urlopen()` from `urllib`.  \n", 'The HTML on the site is pretty broken so we have to do this funky replace to get it to work.  \n', 'Then we create the `tree`.'], ['The first `<table>` on the page is the navigation so we have to use `[1:]` to exclude it'], ['Pretty basic stuff. We define a class `Player` with all the info from the tables.'], ['## Plotting']]


In [49]:
print(''.join(i for i in mdnlist if i))

TypeError: sequence item 0: expected str instance, list found

In [1]:
979097 - 234472

744625